In [1]:
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.by import By
import requests
from selenium.webdriver.support.ui import WebDriverWait
import selenium.webdriver.support.expected_conditions as EC
from tqdm.notebook import tqdm
import time


In [2]:
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument("--incognito")
driver = webdriver.Chrome(executable_path = r"C:\Users\visha\Downloads\chromedriver (2).exe",chrome_options = chrome_options)


C:\Users\visha\AppData\Local\Temp\ipykernel_18972\3189945727.py:3: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(executable_path = r"C:\Users\visha\Downloads\chromedriver (2).exe",chrome_options = chrome_options)
C:\Users\visha\AppData\Local\Temp\ipykernel_18972\3189945727.py:3: DeprecationWarning: use options instead of chrome_options
  driver = webdriver.Chrome(executable_path = r"C:\Users\visha\Downloads\chromedriver (2).exe",chrome_options = chrome_options)


In [3]:
df1 = pd.read_excel(r"C:\Users\visha\Downloads\uk april ams for brand mapping.xlsx")

In [4]:
df1.head(2)

clickedasin                                       producttitle
0  B000000OU2           MTV (Logo) Unplugged In New York [VINYL]
1  B000000XB8  Creedence Clearwater Revival: Vol. 1-Chronicle...

In [5]:
df_ASIN = df1["clickedasin"].copy()
df_ASIN.drop_duplicates(inplace=True)
df_ASIN.dropna(inplace = True)

In [6]:
asinList= list(df_ASIN)
len(asinList)

263766

In [7]:
#asinList1 = list(df_ASIN)
len(asinList)

263766

In [8]:
productDetails = {}

In [9]:
import re

In [10]:
timeout = 10
locator = "imgTagWrapperId"
# productDetails = {}
lastIdx = 0
for val in tqdm(range(25000,30000)):
    try:
   
        i = asinList[val]
        print("i",i)
        productDetails[i] = {}
        lastIdx = val
        link = "https:amazon.co.uk/dp/" + i
        print(link)
        driver.get(link)
        WebDriverWait(driver, timeout).until(EC.visibility_of_element_located((By.ID, locator)))
        try:
            TitleVal = driver.find_element(By.ID,'title')
            productDetails[i]['Title'] = TitleVal.text
            print(TitleVal.text)
        
        except:
            productDetails[i]['Title'] = "Not Found"
            print("Product Title not found")


        try:
            BrandVal = driver.find_element(By.ID,'bylineInfo')
            productDetails[i]['Brand_Subscript'] = BrandVal.text
            print(BrandVal.text)

        except:
            productDetails[i]['Brand_Subscript'] = "Not Found"
            print("Brand from subscript not found")
        
        try:
            Table = driver.find_element(By.ID,'productOverview_feature_div')
            df = pd.read_html(Table.get_attribute("innerHTML"))[0]
            productDetails[i].update(dict(zip(df.iloc[:,0],df.iloc[:,1])))
            print("Product Details",productDetails[i])
        except:
            print("No Product Overview Table Found")
            # productDetails[i] = {}
        try:
            productFeatures = driver.find_element(By.ID,'detailBullets_feature_div')
            features = productFeatures.find_elements(By.TAG_NAME,'li')
            featureDetails = {}
            for j in features:
                featurePair = j.text.split(":")
                try:
                    featureDetails[featurePair[0].strip()] = featurePair[1]
                except:
                    pass
            print("featureDetails",featureDetails)
            productDetails[i].update(featureDetails)
            print("Product Details",productDetails[i])
        except:
            print("featureDetails not found")

        try:
            productFeatures = driver.find_element(By.ID,'detailBulletsWrapper_feature_div')
            features = productFeatures.find_elements(By.TAG_NAME,'li')
            featureDetails1 = {}
            for j in features:
                featurePair = j.text.split(":")
                try:
                    featureDetails1[featurePair[0].strip()] = featurePair[1]
                except:
                    pass
            print("featureDetails",featureDetails1)
            productDetails[i].update(featureDetails1)
            print("Product Details",productDetails[i])
        except:
            print("featureDetails not found")
            
            

        try:
            Table2 = driver.find_element(By.ID,'productDetails_techSpec_section_1')
            technicalDetails = {}
            headers = Table2.find_elements(By.TAG_NAME,'th')
            vals = Table2.find_elements(By.TAG_NAME,'td')
            for k in range(len(headers)):
                try:
                    technicalDetails[headers[k].text.strip()] = vals[k].text
                except:
                    pass
            print("technicalDetails",technicalDetails)
            productDetails[i].update(technicalDetails)
            print(productDetails[i])
        except:
            pass
        try:
            Table3 = driver.find_element(By.ID,'productDetails_detailBullets_sections1')
            dfaDetails = {}
            headers = Table3.find_elements(By.TAG_NAME,'th')
            vals = Table3.find_elements(By.TAG_NAME,'td')
            for k in range(len(headers)):
                try:
                    dfaDetails[headers[k].text.strip()] = vals[k].text
                except:
                    pass
            print("dfaDetails",dfaDetails)
            productDetails[i].update(dfaDetails)
            print(productDetails[i])
        except:
            pass
        try:
            
            SRank = driver.find_element(By.ID,'SalesRank')
            BestSellerRankStr = SRank.text.replace("Amazon Bestsellers Rank: ","")
            BestSellerRankDetails = {'Best Sellers Rank': BestSellerRankStr}
            productDetails[i].update(BestSellerRankDetails)
            print(productDetails[i])
        except:
            pass
        
       #breads 
        
        try:
            bread=driver.find_element(By.ID,"wayfinding-breadcrumbs_feature_div")
            productDetails[i]['cat']=[]
            productDetails[i]['cat_id']=[]
            catss=[]
            catss_id=[]

            links=bread.find_elements_by_tag_name("a")

            for link in links:
                print(link.text)
                catss.append(link.text)
                url = link.get_attribute("href")

                match = re.search(r"node=(\d+)", url)
                node_id = match.group(1)
                catss_id.append(node_id)  
            productDetails[i]['cat']=catss
            productDetails[i]['cat_id']=catss_id
            print(productDetails[i]['cat'])

            
            
        except:      
            productDetails[i]['cat']=[]
            productDetails[i]['cat_id']=[]
            print("no cat found")
        
    except:
        pass

  0%|          | 0/5000 [00:00<?, ?it/s]

i B00ESZW8CQ
https:amazon.co.uk/dp/B00ESZW8CQ
i B00ESZW9AM
https:amazon.co.uk/dp/B00ESZW9AM
i B00ESZWDX0
https:amazon.co.uk/dp/B00ESZWDX0
i B00ESZWGY6
https:amazon.co.uk/dp/B00ESZWGY6
i B00ESZWMQ8
https:amazon.co.uk/dp/B00ESZWMQ8
i B00ESZWXQM
https:amazon.co.uk/dp/B00ESZWXQM
i B00ESZX3TS
https:amazon.co.uk/dp/B00ESZX3TS
i B00ESZXI6Q
https:amazon.co.uk/dp/B00ESZXI6Q
i B00ESZXJKQ
https:amazon.co.uk/dp/B00ESZXJKQ
i B00ESZXNUM
https:amazon.co.uk/dp/B00ESZXNUM
i B00ESZYBKI
https:amazon.co.uk/dp/B00ESZYBKI
i B00ESZYS42
https:amazon.co.uk/dp/B00ESZYS42
i B00ESZYT78
https:amazon.co.uk/dp/B00ESZYT78
i B00ESZYYSM
https:amazon.co.uk/dp/B00ESZYYSM
i B00ESZZKOE
https:amazon.co.uk/dp/B00ESZZKOE
i B00ESZZN2I
https:amazon.co.uk/dp/B00ESZZN2I
i B00ESZZUSK
https:amazon.co.uk/dp/B00ESZZUSK
i B00ESZZVCU
https:amazon.co.uk/dp/B00ESZZVCU
i B00ESZZY86
https:amazon.co.uk/dp/B00ESZZY86
i B00ET00GY2
https:amazon.co.uk/dp/B00ET00GY2
i B00ET0162S
https:amazon.co.uk/dp/B00ET0162S
i B00ET01A8S
https:amazon.co.uk/dp

C:\Users\visha\AppData\Local\Temp\ipykernel_18972\3648537869.py:126: DeprecationWarning: find_elements_by_tag_name is deprecated. Please use find_elements(by=By.TAG_NAME, value=name) instead
  links=bread.find_elements_by_tag_name("a")


Printer Accessories
Inkjet Ink Cartridges
['Printers & Accessories', 'Printer Accessories', 'Inkjet Ink Cartridges']
i B00ET01F88
https:amazon.co.uk/dp/B00ET01F88
i B00ET01FR4
https:amazon.co.uk/dp/B00ET01FR4
Canon Genuine Printer Ink - 1 x PG-545XL High Capacity 15ML Black Ink Cartridge for up to 400 pages - Suitable for Canon PIXMA TR, IP, MX, MG and TS series printers
Visit the Canon Store
Product Details {'Title': 'Canon Genuine Printer Ink - 1 x PG-545XL High Capacity 15ML Black Ink Cartridge for up to 400 pages - Suitable for Canon PIXMA TR, IP, MX, MG and TS series printers', 'Brand_Subscript': 'Visit the Canon Store', 'Model name': 'PG-545', 'Brand': 'Canon', 'Ink colour': 'Black', 'Page yield': '300', 'Compatible devices': 'Printer', 'Special feature': 'Yield:400 pages', 'Compatibility options': 'OEM', 'Colour': 'Black'}
featureDetails not found
featureDetails not found
technicalDetails {'Manufacturer': 'KOMQI', 'Brand': 'Canon', 'Model Number': 'PG-545XL', 'Product Dimensions

C:\Users\visha\AppData\Local\Temp\ipykernel_18972\3648537869.py:126: DeprecationWarning: find_elements_by_tag_name is deprecated. Please use find_elements(by=By.TAG_NAME, value=name) instead
  links=bread.find_elements_by_tag_name("a")


...

Personal Care
Hair Care
['Health & Personal Care', 'Personal Care', 'Hair Care']
i B00HF973EU
https:amazon.co.uk/dp/B00HF973EU
Tassimo Twinings Chai Latte T Discs - 8 Drinks
Visit the Tassimo Store
Product Details {'Title': 'Tassimo Twinings Chai Latte T Discs - 8 Drinks', 'Brand_Subscript': 'Visit the Tassimo Store', 'Brand': 'Tassimo', 'Item form': 'Coffee_discs', 'Flavour': 'Chai', 'Package information': 'Bag', 'Unit count': '8 count', 'Number of items': '8', 'Specialty': 'Alcohol Free', 'Package weight': '0.28 Kilograms'}
featureDetails not found
featureDetails not found
technicalDetails {'Package Dimensions': '20.1 x 14.7 x 7.6 cm; 280 Grams', 'Units': '8 count', 'Brand': 'Tassimo', 'Cuisine': 'English', 'Format': 'Coffee_discs', 'Speciality': 'Alcohol Free', 'Package Information': 'Bag', 'Country of origin': 'United Kingdom'}
{'Title': 'Tassimo Twinings Chai Latte T Discs - 8 Drinks', 'Brand_Subscript': 'Visit the Tassimo Store', 'Brand': 'Tassimo', 'Item form': 'Coffee_discs', '

C:\Users\visha\AppData\Local\Temp\ipykernel_18972\3648537869.py:126: DeprecationWarning: find_elements_by_tag_name is deprecated. Please use find_elements(by=By.TAG_NAME, value=name) instead
  links=bread.find_elements_by_tag_name("a")


Drinks
Coffee
Single-Serve Capsules & Pods
['Drinks', 'Coffee', 'Single-Serve Capsules & Pods']
i B00HFBET8Q
https:amazon.co.uk/dp/B00HFBET8Q
Kelloggs Variety Pack Cereals 8 Pack 6'S (48 Packs)
Visit the Kellogg's Store
No Product Overview Table Found
featureDetails not found
featureDetails not found
technicalDetails {'Package Dimensions': '55.9 x 34.2 x 11.6 cm; 1.77 Kilograms', 'Product Name': 'Food', 'Units': '1146 gram', 'Brand': "Kellogg's", 'Vintage': 'NV', 'Cuisine': 'English', 'Format': 'Flaked', 'Age Range Description': 'Adult', 'Region Produced In': 'Great Britain', 'Speciality': 'Vegetarian', 'Package Information': 'Box', 'Manufacturer': "Kellogg's"}
{'Title': "Kelloggs Variety Pack Cereals 8 Pack 6'S (48 Packs)", 'Brand_Subscript': "Visit the Kellogg's Store", 'Package Dimensions': '55.9 x 34.2 x 11.6 cm; 1.77 Kilograms', 'Product Name': 'Food', 'Units': '1146 gram', 'Brand': "Kellogg's", 'Vintage': 'NV', 'Cuisine': 'English', 'Format': 'Flaked', 'Age Range Description': 'A

C:\Users\visha\AppData\Local\Temp\ipykernel_18972\3648537869.py:126: DeprecationWarning: find_elements_by_tag_name is deprecated. Please use find_elements(by=By.TAG_NAME, value=name) instead
  links=bread.find_elements_by_tag_name("a")


Insect Control
Outdoor Insect Control
Bees, Wasps & Hornets
['Gardening', 'Plant Protection & Pest Control', 'Insect Control', 'Outdoor Insect Control', 'Bees, Wasps & Hornets']
i B00HFDHMBK
https:amazon.co.uk/dp/B00HFDHMBK
i B00HFDHUT4
https:amazon.co.uk/dp/B00HFDHUT4
i B00HFDJ7BS
https:amazon.co.uk/dp/B00HFDJ7BS
i B00HFDJVS2
https:amazon.co.uk/dp/B00HFDJVS2


In [11]:
df_productDetails = pd.DataFrame.from_dict(productDetails,orient='index')

In [12]:
df_productDetails

Title  \
B00ET01F5Q  CANON PG-545 / CL-546 Ink Black and Colour Sta...   
B00ET01FR4  Canon Genuine Printer Ink - 1 x PG-545XL High ...   
B00ET0KV9W  King Cole Big Value Baby DK 100% Acrylic Doubl...   
B00ET0KVVU  King Cole Big Value Baby DK 100% Acrylic Doubl...   
B00ET2LSLK  Canon ink cartridges PG-545+ CLI-546 BK/C/M/Y ...   
...                                                       ...   
B00HF798KE  Supa Mixed Poultry Grit 3 Litre Bucket, A Mixt...   
B00HF91LXE  Garnier Belle Color Black Hair Dye Permanent, ...   
B00HF973EU     Tassimo Twinings Chai Latte T Discs - 8 Drinks   
B00HFBET8Q  Kelloggs Variety Pack Cereals 8 Pack 6'S (48 P...   
B00HFDGMNO  ASPECTEK Wasp Trap - Wasp Catcher, Bee Trap, Y...   

                              Brand_Subscript     Model name  \
B00ET01F5Q              Visit the Canon Store  PG-545/CL-546   
B00ET01FR4              Visit the Canon Store         PG-545   
B00ET0KV9W  Brand: King Cole - King Cole Wool            NaN   
B00ET0KVVU                   Brand: King Cole            NaN   
B00ET2LSLK              Visit the Canon Store            NaN   
...                                       ...            ...   
B00HF798KE               Visit the Supa Store            NaN   
B00HF91LXE            Visit the Garnier Store            NaN   
B00HF973EU            Visit the Tassimo Store            NaN   
B00HFBET8Q          Visit the Kellogg's Store            NaN   
B00HFDGMNO                    Brand: ASPECTEK            NaN   

                                 Brand     Ink colour Page yield  \
B00ET01F5Q                       Canon  Multicoloured        180   
B00ET01FR4                       Canon          Black        300   
B00ET0KV9W  King Cole - King Cole Wool            NaN        NaN   
B00ET0KVVU                   King Cole            NaN        NaN   
B00ET2LSLK                       Canon     Multicolor        180   
...                                ...            ...        ...   
B00HF798KE                        Supa            NaN        NaN   
B00HF91LXE                     Garnier            NaN        NaN   
B00HF973EU                     Tassimo            NaN        NaN   
B00HFBET8Q                   Kellogg's            NaN        NaN   
B00HFDGMNO                    ASPECTEK            NaN        NaN   

           Compatible devices  Special feature  \
B00ET01F5Q            Printer  Yield:180 pages   
B00ET01FR4            Printer  Yield:400 pages   
B00ET0KV9W                NaN              NaN   
B00ET0KVVU                NaN              NaN   
B00ET2LSLK            Printer   Fade Resistant   
...                       ...              ...   
B00HF798KE                NaN              NaN   
B00HF91LXE                NaN              NaN   
B00HF973EU                NaN              NaN   
B00HFBET8Q                NaN              NaN   
B00HFDGMNO                NaN              NaN   

                                        Compatibility options  \
B00ET01F5Q  (function(f) {var _np=(window.P._namespace("De...   
B00ET01FR4                                                OEM   
B00ET0KV9W                                                NaN   
B00ET0KVVU                                                NaN   
B00ET2LSLK                                                OEM   
...                                                       ...   
B00HF798KE                                                NaN   
B00HF91LXE                                                NaN   
B00HF973EU                                                NaN   
B00HFBET8Q                                                NaN   
B00HFDGMNO                                                NaN   

                                Colour  ... Computer Memory Type  \
B00ET01F5Q                Multi-Colour  ...                  NaN   
B00ET01FR4                       Black  ...                  NaN   
B00ET0KV9W                       White  ...                  NaN   
B00ET0KVVU                Sky Blue 

In [13]:
df_productDetails.to_excel(r"nitin.xlsx")